# How to preview a light expert result

This tutorial demonstrates how to review the light expert simulation result.

In [1]:
from pathlib import Path

from ansys.speos.core import LightPathFinder, Project, Speos
from ansys.speos.core.simulation import SimulationInteractive

# If using docker container
assets_data_path = Path("/app") / "assets"
# If using local server
# assets_data_path = Path().resolve().parent.parent / "tests" / "assets"
# If using a different path
# assets_data_path = Path("path/to/downloaded/example/assets")

## Create connection with speos rpc server

In [2]:
speos = Speos(host="localhost", port=50098)

## Create a new project

In this example, a project is created via reading a pre-defined .speos file.

User can preview the part and mesh information.

By providing viz_args to the preview function, project part can be viewed in a semi-transparent
way.

It can be found there is volume conflict in this project.

In [3]:
p = Project(
    speos=speos,
    path=str(assets_data_path / "error_data.speos" / "error_data.speos"),
)
p.preview(viz_args={"opacity": 0.7})

EmbeddableWidget(value='<iframe srcdoc="<!DOCTYPE html>\n<html>\n  <head>\n    <meta http-equiv=&quot;Content-…

## Retrieve the simulation feature and run

In [4]:
sim = p.find("Direct.1")[0]
sim.compute_CPU()

[upload_response {
  info {
    uri: "3e1e04b5-7573-41bf-8dcf-4433bc54b8ba"
    file_name: "Direct.1.Irradiance.1.xmp"
    file_size: 1720632
  }
  upload_duration {
    nanos: 5671582
  }
}
, upload_response {
  info {
    uri: "111e7f3d-4459-4f32-b774-40bd5d891261"
    file_name: "Direct.1.html"
    file_size: 274399
  }
  upload_duration {
    nanos: 652469
  }
}
]

If looking to the simulation report, we will find that we have 40% simulation error

In [5]:
import ansys.speos.core.workflow.open_result as orf

# Methods from workflow class provide a way to find the correct result file.
# Detailed information can be found in the workflow_open_result example.
data = orf._find_correct_result(sim, "Direct.1.html")

## Create a simulation with light expert

We will define an interactive simulation to have a look at the rays in error

In [6]:
interactive_sim = p.create_simulation("error", feature_type=SimulationInteractive)
interactive_sim.set_light_expert(True)
interactive_sim.set_sensor_paths(["Irradiance.1:70"])
interactive_sim.set_source_paths(["Surface.1:4830"])
interactive_sim.commit()

## Preview the light expert result

Here, we will run the simulation and preview the result via LightPathFinder class.

By default, the LightPathFinder class will preview all the rays collected in the simulation.

In [7]:
results = interactive_sim.compute_CPU()
path = orf._find_correct_result(interactive_sim, "error.lpf", download_if_distant=False)
lxp = LightPathFinder(speos, path)
lxp.preview(project=p)

EmbeddableWidget(value='<iframe srcdoc="<!DOCTYPE html>\n<html>\n  <head>\n    <meta http-equiv=&quot;Content-…

## Preview the light expert result with error filter

ray_filter option is provided in the preview function that user can filter the rays to see only
rays in error.

In this example, error rays are generated due to a volume conflict between two solids.

In [8]:
lxp.filter_error_rays()
lxp.preview(project=p, ray_filter=True)

EmbeddableWidget(value='<iframe srcdoc="<!DOCTYPE html>\n<html>\n  <head>\n    <meta http-equiv=&quot;Content-…

In [9]:
speos.close()

True